In [1]:
import zipfile
import os
import pandas as pd
import numpy as np
import os
import sys

In [2]:
print(os.getcwd())

c:\Users\ntama\Documentos\Data Science\My Projects\breast-cancer-gene-test\notebooks


### Dataset X (predictores) Matriz de expresión genética:
contiene los datos de expresión génica para las 3273 muestras y 136 réplicas técnicas. Este será tu conjunto de predictores. Total 3409 muestras. </br>
Los datos de secuencia brutos (raw data) no están disponibles públicamente debido a la ley sueca, la privacidad de los pacientes y el potencial de información de identificación personal y mutaciones hereditarias. Por lo tanto, se trabaja con los datos de expresión procesados.

### Dataset y (targets):
Los targets que se busca predecir son los cinco biomarcadores convencionales del cáncer de mama: receptor de estrógeno (ER), receptor de progesterona (PgR), receptor 2 del factor de crecimiento epidérmico humano (HER2), Ki67 y grado histológico de Nottingham (NHG). El estudio desarrolló clasificadores para estos biomarcadores basándose en etiquetas de histopatología de consenso

In [4]:
gene_exp_df = pd.read_csv("../raw/GSE96058.csv.gz")


## Serie GSE96058 que contiene los targets
Dos archivos:</br>
GSE96058-GPL11154_series_matrix.txt.gz </br>
GSE96058-GPL18573_series_matrix.txt.gz


### Exploración del archivo GSE96058-GPL11154_series_matrix.txt.gz

Metadatos

In [7]:
import gzip

with gzip.open("../raw/GSE96058-GPL18573_series_matrix.txt.gz", "rt") as f: 
    for line in f:
        if line.startswith("!"):
            print(line.strip())

!Series_title	"Clinical Value of RNA Sequencingâ€“Based Classifiers for Prediction of the Five Conventional Breast Cancer Biomarkers: A Report From the Population-Based Multicenter Sweden Cancerome Analysis Networkâ€”Breast Initiative [cohort 3273]"
!Series_geo_accession	"GSE96058"
!Series_status	"Public on Mar 12 2018"
!Series_submission_date	"Mar 09 2017"
!Series_last_update_date	"May 04 2022"
!Series_pubmed_id	"32913985"
!Series_pubmed_id	"32926574"
!Series_pubmed_id	"33937624"
!Series_pubmed_id	"35304506"
!Series_summary	"PURPOSE"
!Series_summary	"In early breast cancer (BC), five conventional biomarkersâ€”estrogen receptor (ER), progesterone receptor (PgR), human epidermal growth factor receptor 2 (HER2), Ki67, and Nottingham histologic grade (NHG)â€”are used to determine prognosis and treatment. We aimed to develop classifiers for these biomarkers that were based on tumor mRNA sequencing (RNA-seq), compare classification performance, and test whether such predictors could add val

### Exploración del archivo GSE96058-GPL18573_series_matrix.txt.gz
Metadatos


In [8]:
with gzip.open("../raw/GSE96058-GPL18573_series_matrix.txt.gz", "rt") as f:
    for line in f:
        if line.startswith("!"):
            print(line.strip())

!Series_title	"Clinical Value of RNA Sequencingâ€“Based Classifiers for Prediction of the Five Conventional Breast Cancer Biomarkers: A Report From the Population-Based Multicenter Sweden Cancerome Analysis Networkâ€”Breast Initiative [cohort 3273]"
!Series_geo_accession	"GSE96058"
!Series_status	"Public on Mar 12 2018"
!Series_submission_date	"Mar 09 2017"
!Series_last_update_date	"May 04 2022"
!Series_pubmed_id	"32913985"
!Series_pubmed_id	"32926574"
!Series_pubmed_id	"33937624"
!Series_pubmed_id	"35304506"
!Series_summary	"PURPOSE"
!Series_summary	"In early breast cancer (BC), five conventional biomarkersâ€”estrogen receptor (ER), progesterone receptor (PgR), human epidermal growth factor receptor 2 (HER2), Ki67, and Nottingham histologic grade (NHG)â€”are used to determine prognosis and treatment. We aimed to develop classifiers for these biomarkers that were based on tumor mRNA sequencing (RNA-seq), compare classification performance, and test whether such predictors could add val

### Explorando gene_exp_df

In [9]:
gene_exp_df.head()

Unnamed: 0        F1        F2        F3        F4        F5        F6  \
0  5_8S_rRNA -3.321928 -3.321928 -3.321928 -3.321928 -3.321928 -3.321928   
1    5S_rRNA  4.911099 -3.321928 -3.321928  3.656393  4.190104  2.556304   
2     6M1-18 -3.321928 -3.321928 -3.321928 -3.321928 -3.321928 -3.321928   
3      7M1-2 -3.321928 -3.321928 -3.321928 -3.321928 -3.321928 -3.321928   
4        7SK -0.539253 -0.576620 -1.651323  0.126633  0.783715 -1.759556   

         F7        F8        F9  ...  F2974repl  F3006repl  F3028repl  \
0 -3.321928 -3.321928 -3.321928  ...  -3.321928  -3.321928  -3.321928   
1  2.590351  5.691788 -3.321928  ...   4.084251   2.287523   3.205371   
2 -3.321928 -3.321928 -3.321928  ...  -3.321928  -3.321928  -3.321928   
3 -3.321928 -3.321928 -3.321928  ...  -3.321928  -3.321928  -3.321928   
4 -1.033968 -0.129513  0.494308  ...   0.233159  -0.026301   1.249039   

   F3057repl  F3058repl  F3085repl  F3127repl  F3135repl  F3250repl  F3265repl  
0  -3.321928  -3.321928  -3.321928  -3.321928  -3.321928  -3.321928  -3.321928  
1   6.965451  -3.321928   4.531984  -3.321928   5.097337   1.895737   2.954997  
2  -3.321928  -3.321928  -3.321928  -3.321928  -3.321928  -3.321928  -3.321928  
3  -3.321928  -3.321928  -3.321928  -3.321928  -3.321928  -3.321928  -3.321928  
4   1.651384   0.128604  -0.594062  -0.228405   0.239723   2.074377   0.867608  

[5 rows x 3410 columns]

Antes de trasponer, se verifica que ninguna muestra tiene datos faltantes en genes

In [10]:
gexp_columns = gene_exp_df.columns

missing_samples = []
for col in gexp_columns:
    if np.sum(gene_exp_df[col].isnull()) > 0:
        missing_samples.append(col)

print(missing_samples)



[]


Aquí se observa que no hay muestras con datos faltantes en el perfil genético

### Trasposición de gene_exp_df
Cada FXX es una muestra, cada Unnamed: 0 es un gen. </br>
Por lo tanto, X debe trasponerse

In [127]:
gene_exp_df = gene_exp_df.T.reset_index()
gene_exp_df.head()

index          0         1         2         3         4         5  \
0  Unnamed: 0  5_8S_rRNA   5S_rRNA    6M1-18     7M1-2       7SK      A1BG   
1          F1  -3.321928  4.911099 -3.321928 -3.321928 -0.539253  0.598115   
2          F2  -3.321928 -3.321928 -3.321928 -3.321928  -0.57662  2.363673   
3          F3  -3.321928 -3.321928 -3.321928 -3.321928 -1.651323  2.647738   
4          F4  -3.321928  3.656393 -3.321928 -3.321928  0.126633  1.378576   

          6         7         8  ...     30855     30856     30857     30858  \
0  A1BG-AS1      A1CF       A2M  ...    ZWILCH     ZWINT      ZXDA      ZXDB   
1 -1.352525 -3.213583  6.172477  ...  1.108204  3.044573  1.640598  2.425306   
2  -0.77943 -3.054421  7.113514  ...  1.678388  2.743902   0.68437  1.861781   
3   0.08541 -3.321928  5.641996  ...  2.443392  4.719843 -0.160076  1.365396   
4 -0.334324 -3.321928  7.236769  ...  2.441704  4.157466  1.036271  2.038984   

      30859     30860     30861     30862     30863     30864  
0      ZXDC    ZYG11A    ZYG11B       ZYX     ZZEF1      ZZZ3  
1  3.244432  -0.41195  1.468899  6.281767  1.774107  2.437227  
2  2.727427 -0.452902  1.924761  7.169613  1.764214    2.8761  
3  3.122333  0.594147  1.619277    6.6834  2.039246  2.929346  
4  3.182823 -0.046619  1.969433  6.666306   2.77165  2.777674  

[5 rows x 30866 columns]

In [128]:
#quitando los índices después de la trasposición
gene_exp_df.columns = gene_exp_df.iloc[0]

gene_exp_df = gene_exp_df.drop(gene_exp_df.index[0])

gene_exp_df = gene_exp_df.reset_index(drop=True)

In [129]:
gene_exp_df.rename(columns={'Unnamed: 0': 'SampleID'}, inplace=True)
gene_exp_df.head()

0 SampleID 5_8S_rRNA   5S_rRNA    6M1-18     7M1-2       7SK      A1BG  \
0       F1 -3.321928  4.911099 -3.321928 -3.321928 -0.539253  0.598115   
1       F2 -3.321928 -3.321928 -3.321928 -3.321928  -0.57662  2.363673   
2       F3 -3.321928 -3.321928 -3.321928 -3.321928 -1.651323  2.647738   
3       F4 -3.321928  3.656393 -3.321928 -3.321928  0.126633  1.378576   
4       F5 -3.321928  4.190104 -3.321928 -3.321928  0.783715  2.759643   

0  A1BG-AS1      A1CF       A2M  ...    ZWILCH     ZWINT      ZXDA      ZXDB  \
0 -1.352525 -3.213583  6.172477  ...  1.108204  3.044573  1.640598  2.425306   
1  -0.77943 -3.054421  7.113514  ...  1.678388  2.743902   0.68437  1.861781   
2   0.08541 -3.321928  5.641996  ...  2.443392  4.719843 -0.160076  1.365396   
3 -0.334324 -3.321928  7.236769  ...  2.441704  4.157466  1.036271  2.038984   
4  0.984849 -3.321928  7.508171  ...   1.74923   1.02482  1.147535  2.032704   

0      ZXDC    ZYG11A    ZYG11B       ZYX     ZZEF1      ZZZ3  
0  3.244432  -0.41195  1.468899  6.281767  1.774107  2.437227  
1  2.727427 -0.452902  1.924761  7.169613  1.764214    2.8761  
2  3.122333  0.594147  1.619277    6.6834  2.039246  2.929346  
3  3.182823 -0.046619  1.969433  6.666306   2.77165  2.777674  
4  3.588842  0.808823  2.998474  6.479006  2.696269  3.957146  

[5 rows x 30866 columns]

In [130]:
print(f"El conjunto 'gene_exp_df' tiene un total de {len(gene_exp_df)} registros")

El conjunto 'gene_exp_df' tiene un total de 3409 registros


## Parseo de los datos clínicos:
GSE96058-GPL11154_series_matrix.txt.gz </br>
GSE96058-GPL18573_series_matrix.txt.gz </br>

En búsqueda de los targets </br>
Cada muestra (F7, F30repl, etc.) tiene asociados 6 targets potenciales:

- ER: Estrogen receptor
- PgR: Progesterone receptor
- HER2: Receptor 2 del factor de crecimiento epidérmico humano
- Ki67
- NHG (Nottingham Histologic Grade, 3 clases → bueno para multiclase)
- PAM50 (subtipos moleculares → otra multiclase).

Las líneas que contienen el "!Sample_title" se corresponden con los IDs de las muestras (F1, F2, ...)</br>
Las líneas que contengan el "!Sample_characteristics_ch1" se corresponden con los targets

#### Definición de la función para el parseo

In [131]:
def parse_series_matrix(file_path):
    with gzip.open(file_path, "rt") as f:
        lines = [l.strip() for l in f if l.startswith("!Sample_")]

    # títulos de muestras
    sample_titles = [l.split("\t")[1:] for l in lines if l.startswith("!Sample_title")][0]

    metadata = {"SampleID": sample_titles}

    # recorrer características
    for line in lines:
        if line.startswith("!Sample_characteristics_ch1"):
            parts = line.split("\t")[1:]  # ignorar "!Sample_characteristics_ch1"
            # el nombre de la característica está antes de los ":"
            first_val = parts[0]
            if ":" in first_val:
                key = first_val.split(":")[0].strip()
                values = [p.split(":",1)[1].strip() if ":" in p else p for p in parts]
                metadata[key] = values

    return pd.DataFrame(metadata)

#### Parseo del GSE96058-GPL11154_series_matrix.txt.gz

In [132]:
file_path_1154 = "raw/GSE96058-GPL11154_series_matrix.txt.gz"
metadata_1154 = parse_series_matrix(file_path=file_path_1154)
metadata_1154.head()

SampleID                            "scan-b external id "instrument model  \
0     "F1"  Q008818.C008840.S000215.l.r.m2.c.lib.g.k.a.t"       HiSeq 2000"   
1     "F2"   Q008769.C008792.S000250.l.r.m.c.lib.g.k.a.t"       HiSeq 2000"   
2     "F3"  Q008568.C008577.S000424.l.r.m3.c.lib.g.k.a.t"       HiSeq 2000"   
3     "F4"   Q008909.C009000.S000084.l.r.m.c.lib.g.k.a.t"       HiSeq 2000"   
4     "F5"   Q008781.C008782.S000260.l.r.m.c.lib.g.k.a.t"       HiSeq 2000"   

  "age at diagnosis "tumor size "lymph node group "lymph node status  \
0               43"          9"     NodeNegative"      NodeNegative"   
1               48"         14"             1to3"      NodePositive"   
2               69"         27"             4toX"      NodePositive"   
3               39"         51"             1to3"      NodePositive"   
4               73"         60"             4toX"      NodePositive"   

  "er status "pgr status "her2 status  ... "nhg prediction mgc  \
0        NA"         NA"           0"  ...                 G3"   
1         1"          1"           0"  ...                 G2"   
2         1"          1"           0"  ...                 G3"   
3         1"         NA"           1"  ...                 G3"   
4         1"         NA"           0"  ...                 G2"   

  "er prediction sgc "pgr prediction sgc "her2 prediction sgc  \
0                 0"                  0"                   0"   
1                 1"                  1"                   0"   
2                 1"                  1"                   0"   
3                 1"                  1"                   1"   
4                 1"                  1"                   0"   

  "ki67 prediction sgc "pam50 subtype "overall survival days  \
0                   1"         Basal"                  2367"   
1                   0"          LumA"                  2367"   
2                   1"          LumB"                  2168"   
3                   1"          LumA"                  2416"   
4                   0"        Normal"                  2389"   

  "overall survival event "endocrine treated "chemo treated  
0                      0"                 0"             1"  
1                      0"                 1"             1"  
2                      1"                 1"             1"  
3                      0"                 1"             1"  
4                      0"                 1"             0"  

[5 rows x 26 columns]

Limpieza de las columnas

In [133]:
# Limpiar nombres de columnas
metadata_1154.rename(columns=lambda x: x.replace('"', ''), inplace=True)

# Limpiar valores en todas las columnas de tipo string (object)
for col in metadata_1154.select_dtypes(include=['object']):
    metadata_1154[col] = metadata_1154[col].str.replace('"', '', regex=False)

metadata_1154.head()

SampleID                            scan-b external id instrument model  \
0       F1  Q008818.C008840.S000215.l.r.m2.c.lib.g.k.a.t       HiSeq 2000   
1       F2   Q008769.C008792.S000250.l.r.m.c.lib.g.k.a.t       HiSeq 2000   
2       F3  Q008568.C008577.S000424.l.r.m3.c.lib.g.k.a.t       HiSeq 2000   
3       F4   Q008909.C009000.S000084.l.r.m.c.lib.g.k.a.t       HiSeq 2000   
4       F5   Q008781.C008782.S000260.l.r.m.c.lib.g.k.a.t       HiSeq 2000   

  age at diagnosis tumor size lymph node group lymph node status er status  \
0               43          9     NodeNegative      NodeNegative        NA   
1               48         14             1to3      NodePositive         1   
2               69         27             4toX      NodePositive         1   
3               39         51             1to3      NodePositive         1   
4               73         60             4toX      NodePositive         1   

  pgr status her2 status  ... nhg prediction mgc er prediction sgc  \
0         NA           0  ...                 G3                 0   
1          1           0  ...                 G2                 1   
2          1           0  ...                 G3                 1   
3         NA           1  ...                 G3                 1   
4         NA           0  ...                 G2                 1   

  pgr prediction sgc her2 prediction sgc ki67 prediction sgc pam50 subtype  \
0                  0                   0                   1         Basal   
1                  1                   0                   0          LumA   
2                  1                   0                   1          LumB   
3                  1                   1                   1          LumA   
4                  1                   0                   0        Normal   

  overall survival days overall survival event endocrine treated chemo treated  
0                  2367                      0                 0             1  
1                  2367                      0                 1             1  
2                  2168                      1                 1             1  
3                  2416                      0                 1             1  
4                  2389                      0                 1             0  

[5 rows x 26 columns]

Dimensiones del GSE96058-GPL11154_series_matrix.txt.gz

In [134]:
print(f"El conjunto 'GSE96058-GPL11154_series_matrix.txt.gz' tiene un total de {metadata_1154.shape} registros")

El conjunto 'GSE96058-GPL11154_series_matrix.txt.gz' tiene un total de (3069, 26) registros


#### Parseo del GSE96058-GPL18573_series_matrix.txt.gz

In [135]:
file_path_8573 = "raw/GSE96058-GPL18573_series_matrix.txt.gz"
metadata_8573 = parse_series_matrix(file_path=file_path_8573)
metadata_8573.head()

SampleID                             "scan-b external id "instrument model  \
0     "F7"   Q008861.C008874.S000184.l2.r.m.c.lib.g.k.a.t"      NextSeq 500"   
1     "F8"  Q008860.C008864.S000189.l2.r.m2.c.lib.g.k.a.t"      NextSeq 500"   
2   "F142"    Q007079.C007100.S002089.l.r.m.c.lib.g.k.a.t"      NextSeq 500"   
3   "F185"    Q007294.C007301.S001422.l.r.m.c.lib.g.k.a.t"      NextSeq 500"   
4   "F219"    Q006932.C006926.S002180.l.r.m.c.lib.g.k.a.t"      NextSeq 500"   

  "age at diagnosis "tumor size "lymph node group "lymph node status  \
0               58"         18"     NodeNegative"      NodeNegative"   
1               56"         24"             1to3"      NodePositive"   
2               46"          2"     NodeNegative"      NodeNegative"   
3               45"         13"     NodeNegative"      NodeNegative"   
4               81"         17"     NodeNegative"      NodeNegative"   

  "er status "pgr status "her2 status  ... "nhg prediction mgc  \
0         1"         NA"           0"  ...                 G2"   
1         1"          1"           0"  ...                 G2"   
2        NA"         NA"          NA"  ...                 G3"   
3         1"          1"           0"  ...                 G2"   
4         1"          1"           0"  ...                 G2"   

  "er prediction sgc "pgr prediction sgc "her2 prediction sgc  \
0                 1"                  1"                   0"   
1                 1"                  1"                   0"   
2                 0"                  0"                   0"   
3                 1"                  1"                   0"   
4                 1"                  1"                   0"   

  "ki67 prediction sgc "pam50 subtype "overall survival days  \
0                   0"        Normal"                  2410"   
1                   0"        Normal"                  2388"   
2                   1"         Basal"                  1893"   
3                   1"          LumA"                  1950"   
4                   0"          LumA"                  1881"   

  "overall survival event "endocrine treated "chemo treated  
0                      0"                 1"             0"  
1                      0"                 1"             1"  
2                      0"                 0"             0"  
3                      0"                 1"             0"  
4                      0"                 0"             0"  

[5 rows x 26 columns]

Limpieza de las columnas

In [136]:
# Limpiar nombres de columnas
metadata_8573.rename(columns=lambda x: x.replace('"', ''), inplace=True)

# Limpiar valores en todas las columnas de tipo string (object)
for col in metadata_8573.select_dtypes(include=['object']):
    metadata_8573[col] = metadata_8573[col].str.replace('"', '', regex=False)

metadata_8573.head()

SampleID                             scan-b external id instrument model  \
0       F7   Q008861.C008874.S000184.l2.r.m.c.lib.g.k.a.t      NextSeq 500   
1       F8  Q008860.C008864.S000189.l2.r.m2.c.lib.g.k.a.t      NextSeq 500   
2     F142    Q007079.C007100.S002089.l.r.m.c.lib.g.k.a.t      NextSeq 500   
3     F185    Q007294.C007301.S001422.l.r.m.c.lib.g.k.a.t      NextSeq 500   
4     F219    Q006932.C006926.S002180.l.r.m.c.lib.g.k.a.t      NextSeq 500   

  age at diagnosis tumor size lymph node group lymph node status er status  \
0               58         18     NodeNegative      NodeNegative         1   
1               56         24             1to3      NodePositive         1   
2               46          2     NodeNegative      NodeNegative        NA   
3               45         13     NodeNegative      NodeNegative         1   
4               81         17     NodeNegative      NodeNegative         1   

  pgr status her2 status  ... nhg prediction mgc er prediction sgc  \
0         NA           0  ...                 G2                 1   
1          1           0  ...                 G2                 1   
2         NA          NA  ...                 G3                 0   
3          1           0  ...                 G2                 1   
4          1           0  ...                 G2                 1   

  pgr prediction sgc her2 prediction sgc ki67 prediction sgc pam50 subtype  \
0                  1                   0                   0        Normal   
1                  1                   0                   0        Normal   
2                  0                   0                   1         Basal   
3                  1                   0                   1          LumA   
4                  1                   0                   0          LumA   

  overall survival days overall survival event endocrine treated chemo treated  
0                  2410                      0                 1             0  
1                  2388                      0                 1             1  
2                  1893                      0                 0             0  
3                  1950                      0                 1             0  
4                  1881                      0                 0             0  

[5 rows x 26 columns]

Dimensiones del GSE96058-GPL18573_series_matrix.txt.gz

In [137]:
print(f"El conjunto 'GSE96058-GPL18573_series_matrix.txt.gz' tiene un total de {metadata_8573.shape} registros")

El conjunto 'GSE96058-GPL18573_series_matrix.txt.gz' tiene un total de (340, 26) registros


`NOTA IMPORTANTE:` Las series con sufijos designados 1154 y 8573 conforman 3409 registros realizados con la tecnología de secuenciación HiSeq 2000 y 340 registros con la tenología NextSeq 500, comprenden un total de 3409 registros, lo cual coincide con la cantidad de registros de la expresión génica

### Descripción de las variables

| Columna                             | Significado                                                                                                                | Tipo / Uso en ML                                                             |
| ----------------------------------- | -------------------------------------------------------------------------------------------------------------------------- | ---------------------------------------------------------------------------- |
| **SampleID**                        | ID interno del dataset (ej. `F1`, `F2`…)                                                                                   | Clave primaria para merge con la expresión génica.                        |
| **scan-b external id**              | Identificador externo del proyecto SCAN-B (ej. `Q008818.C008840…`).                                                        | Normalmente no se usa como feature.                                          |
| **instrument model**                | Tecnología de secuenciación (ej. `HiSeq 2000`, `NextSeq 500`).                                                                            | Constante en este estudio, poco útil.                                        |
| **age at diagnosis**                | Edad de la paciente al diagnóstico.                                                                                        | Numérico, clínicamente relevante.                                            |
| **tumor size**                      | Tamaño del tumor en mm.                                                                                                    | Numérico, predictor clásico.                                                 |
| **lymph node group**                | Categoría de ganglios afectados (ej. `NodeNegative`, `1to3`, `4toX`).                                                      | Categórico ordinal, importante clínicamente.                                 |
| **lymph node status**               | Simplificación binaria de lo anterior (`NodePositive`, `NodeNegative`).                                                    | Binario, predictor simple.                                                   |
| **er status**                       | Estado del receptor de estrógeno (ER). `1 = positivo`, `0 = negativo`, `NA = faltante`.                                    | Binario, *target* frecuente.                                                 |
| **pgr status**                      | Estado del receptor de progesterona (PgR). `1 = positivo`, `0 = negativo`.                                                 | Binario.                                                                     |
| **her2 status**                     | Estado de HER2 (proto-oncogén). `1 = positivo`, `0 = negativo`.                                                            | Binario.                                                                     |
| **nhg prediction mgc**              | Predicción del **Nottingham Histologic Grade (NHG)** por un clasificador molecular (`MGC`). Valores como `G1`, `G2`, `G3`. | Categórico ordinal (multiclase de 3). **Muy usado como target en papers.**   |
| **er/pgr/her2/ki67 prediction sgc** | Predicciones moleculares (Single Gene Classifier, `SGC`) de biomarcadores. (`0/1`).                                        | Útiles si quieres comparar predicciones moleculares vs. status clínico real. |
| **pam50 subtype**                   | Clasificación molecular en 5 subtipos (`LumA`, `LumB`, `HER2`, `Basal`, `Normal`).                                         | Multiclase de alto interés biológico.                                        |
| **overall survival days**           | Tiempo de seguimiento de la paciente (en días).                                                                            | Numérico. Usable en modelos de supervivencia (*Cox regression*).             |
| **overall survival event**          | Estado vital al final del seguimiento (`1 = fallecida`, `0 = viva`).                                                       | Binario, para modelos de predicción de supervivencia.                        |
| **endocrine treated**               | Si recibió tratamiento endocrino (`1 = sí`, `0 = no`).                                                                     | Binario, covariable.                                                         |
| **chemo treated**                   | Si recibió quimioterapia (`1 = sí`, `0 = no`).                                                                             | Binario, covariable.                                                         |


##### Uso de los datos de expresión génica:.

- High-dimensional ML → Los perfiles de expresión (miles de genes) son features masivos.

- Permiten aplicar clustering, PCA, autoencoders y técnicas de reducción de dimensionalidad.
Ejemplo: Agrupación de 5 clusters que coinciden con subtipos PAM50

- Predicción biológica real → En la práctica, la clínica quiere modelos que predigan subtipo, grado histológico o supervivencia directamente de la expresión génica, no de variables clínicas que ya están disponibles.

El modelo puede responder: “Dado solo el RNA-seq, ¿se puede predecir el NHG o el subtipo PAM50?”.

### Alcance del problema:

- Predicción del NHG (Nothingham Histologic Grade) por un clasificador molecular (MGC): Multiclase de 3 valores (``G1``, ``G2``, ``G3``) a partir del perfil de expresión génica.
- Predicción del PAM50 subtype: Clasificación molecular en 5 subtipos (``LumA``, ``LumB``, ``HER2``,`` Basal``, ``Normal``) a partir del perfil de expresión génica.

- Modelo de supervivencia Cox regression (Overall survival days) con los datos clínicos

### Concatenación de los datos clínicos

In [138]:
clinic_data = pd.concat([metadata_1154, metadata_8573], axis=0, ignore_index=True)

### Generación del conjunto de datos para el primer estudio:
Predicción del NHG

In [141]:
clinic_data_nhg = clinic_data[['SampleID', 'nhg prediction mgc']]
gene_nhg = pd.merge(gene_exp_df, clinic_data_nhg, on='SampleID', how='inner')
gene_nhg.head()

SampleID 5_8S_rRNA   5S_rRNA    6M1-18     7M1-2       7SK      A1BG  \
0       F1 -3.321928  4.911099 -3.321928 -3.321928 -0.539253  0.598115   
1       F2 -3.321928 -3.321928 -3.321928 -3.321928  -0.57662  2.363673   
2       F3 -3.321928 -3.321928 -3.321928 -3.321928 -1.651323  2.647738   
3       F4 -3.321928  3.656393 -3.321928 -3.321928  0.126633  1.378576   
4       F5 -3.321928  4.190104 -3.321928 -3.321928  0.783715  2.759643   

   A1BG-AS1      A1CF       A2M  ...     ZWINT      ZXDA      ZXDB      ZXDC  \
0 -1.352525 -3.213583  6.172477  ...  3.044573  1.640598  2.425306  3.244432   
1  -0.77943 -3.054421  7.113514  ...  2.743902   0.68437  1.861781  2.727427   
2   0.08541 -3.321928  5.641996  ...  4.719843 -0.160076  1.365396  3.122333   
3 -0.334324 -3.321928  7.236769  ...  4.157466  1.036271  2.038984  3.182823   
4  0.984849 -3.321928  7.508171  ...   1.02482  1.147535  2.032704  3.588842   

     ZYG11A    ZYG11B       ZYX     ZZEF1      ZZZ3 nhg prediction mgc  
0  -0.41195  1.468899  6.281767  1.774107  2.437227                 G3  
1 -0.452902  1.924761  7.169613  1.764214    2.8761                 G2  
2  0.594147  1.619277    6.6834  2.039246  2.929346                 G3  
3 -0.046619  1.969433  6.666306   2.77165  2.777674                 G3  
4  0.808823  2.998474  6.479006  2.696269  3.957146                 G2  

[5 rows x 30867 columns]

### Generación del conjunto de datos para el segundo estudio:
Predicción del PAM50 subtype

In [142]:
clinic_data_pam50 = clinic_data[['SampleID', 'pam50 subtype']]
gene_pam50 = pd.merge(gene_exp_df, clinic_data_pam50, on='SampleID', how='inner')
gene_pam50.head()

SampleID 5_8S_rRNA   5S_rRNA    6M1-18     7M1-2       7SK      A1BG  \
0       F1 -3.321928  4.911099 -3.321928 -3.321928 -0.539253  0.598115   
1       F2 -3.321928 -3.321928 -3.321928 -3.321928  -0.57662  2.363673   
2       F3 -3.321928 -3.321928 -3.321928 -3.321928 -1.651323  2.647738   
3       F4 -3.321928  3.656393 -3.321928 -3.321928  0.126633  1.378576   
4       F5 -3.321928  4.190104 -3.321928 -3.321928  0.783715  2.759643   

   A1BG-AS1      A1CF       A2M  ...     ZWINT      ZXDA      ZXDB      ZXDC  \
0 -1.352525 -3.213583  6.172477  ...  3.044573  1.640598  2.425306  3.244432   
1  -0.77943 -3.054421  7.113514  ...  2.743902   0.68437  1.861781  2.727427   
2   0.08541 -3.321928  5.641996  ...  4.719843 -0.160076  1.365396  3.122333   
3 -0.334324 -3.321928  7.236769  ...  4.157466  1.036271  2.038984  3.182823   
4  0.984849 -3.321928  7.508171  ...   1.02482  1.147535  2.032704  3.588842   

     ZYG11A    ZYG11B       ZYX     ZZEF1      ZZZ3 pam50 subtype  
0  -0.41195  1.468899  6.281767  1.774107  2.437227         Basal  
1 -0.452902  1.924761  7.169613  1.764214    2.8761          LumA  
2  0.594147  1.619277    6.6834  2.039246  2.929346          LumB  
3 -0.046619  1.969433  6.666306   2.77165  2.777674          LumA  
4  0.808823  2.998474  6.479006  2.696269  3.957146        Normal  

[5 rows x 30867 columns]

### Tercer estudio:
Modelo de supervivencia Cox regression con datos clínicos, se usará 'clinic_data'

### Exportación de los conjuntos de datos a csv

In [ ]:
gene_nhg.to_csv("gene_nhg.csv", index=False)
gene_pam50.to_csv("gene_pam50.csv", index=False)
clinic_data.to_csv("clinic_data.csv", index=False)